# TP 4 : récursion

Dans ce TP :

1. Principe des fonctions récursives
2. Etude de cas : nombres de Stirling et dictionnaires
   




## 1 - La récursion

#### Principes des fonctions récursives

Quand on a défini une nouvelle fonction `f`, on peut l'appeler à tout moment -- Python remplace `f(x)` par le code que nous avons donné dans la définition. Une chose qui peut paraître étonnante au début, c'est qu'on peut appeler `f` au sein même de sa définition. Voici l'exemple que l'on donne toujours.


In [ ]:
def factorielle(n):
    """Calcule n!= n(n-1)(n-2)...3*2*1."""
    
    if n <= 1:
        return 1
    else:
        return n*factorielle(n-1)
    

In [ ]:
factorielle(1000)

Mathématiquement, on peut passer beaucoup de temps à se demander si utiliser $f$ pendant qu'on est en train de définir $f$ a vraiment un sens. En informatique, tout est beaucoup plus simple : quand Python voit un appel à `f` dans la définition de `f`, tout simplement, *il y va*. L'observateur humain dit alors que `f` est une fonction "récursive", mais pour Python, c'est juste une fonction, qui se trouve par hasard faire un appel à elle-même.

(Ceci est un petit mensonge ; les gens qui ont inventé le langage Python, et qui continuent de le faire évoluer, ont très certainement mis en place divers mécanismes pour optimiser l'exécution des fonctions récursives. Mais en principe, il n'y aurait pas vraiment besoin.)

Le prix à payer est que Python nous autorise à écrire des choses aux conséquences catastrophiques : remplacez la fin de la définition par `n*factorielle(n+1)` et l'ordinateur va tourner sans fin jusqu'à épuisement de la mémoire!




Pour s'entraîner à écrire une fonction récursive, voici maintenant l'exercice que l'on donne toujours.

>**Exercice (Fibonacci)** Ecrire une fonction `fibonacci(n)` qui renvoie le terme $u_n$ de la suite définie par
>
> $ u_0 = u_1 = 1, \qquad\qquad$    $u_{n} = u_{n-1} + u_{n-2}$ pour $n\ge 2$.
>
> Examiner le quotient $\frac{u_{n+1}} {u_n}$ à mesure que $n$ augmente.



Un exemple très classique est l'algorithme d'Euclide pour calculer les pgcd. Vous l'avez déjà vu, mais rappelons qu'il se base sur la remarque simple suivante : si on écrit la division euclidienne

$a= bq + r$

de $a$ par $b\ne 0$, alors $pgcd(a,b) = pgcd(b,r)$. Et aussi, $pgcd(a,0) = a$.

La traduction en Python est immédiate :

In [ ]:
def pgcd(a,b):
    if b == 0:
        return a
    else:
        r= a % b
        return pgcd(b,r)

In [ ]:
pgcd(24, 15)

>**Exercice (Bézout)** Ecrire une fonction `bezout(a,b)` qui renvoie une liste `[d, u, v]` où $d$ est le pgcd des entiers $a$ et $b$, et les entiers $u$ et $v$ vérifient $au +bv = d$.
>
>**Indication.** Faire d'abord une fonction auxiliaire, disons `bezout_aux(A,B,uA,vA,uB,vB)` qui prend en entrée six entiers, avec la propriété que $A= a u_A + bv_A$ et de même $B= a u_B + b v_B$, et qui renvoie `[d, u, v]`, où $d= pgcd(A,B)$ et $d = au + bv$. On fait ça de manière récursive, en commençant par "si $B=0$ c'est évident, et sinon...".
>
>Ensuite `bezout(a, b) = bezout_aux(a,b,1,0,0,1)`. A noter que `bezout_aux` ne prend pas $a$ et $b$ comme paramètre, il se trouve (un peu par hasard) qu'elle n'en a pas besoin.
>
> Facultatif : pourriez-vous ajouter des `print` bien sentis pour que l'on ait l'impression de lire la copie de quelqu'un qui ferait ce calcul "à la main" ? 

Exercice supplémentaire :

>**Exercice (les défauts de la factorielle)** Vérifier que la fonction factorielle ci-dessus "plante" pour des valeurs de $n$ trop grandes (avec un $n \le 10000$ ça devrait déjà arriver). A moins que vous n'ayez essayé des valeurs de $n$ vraiment délirantes, le plantage n'est pas dû à un manque de mémoire ; vous avez plutôt :
>
`RecursionError: maximum recursion depth exceeded in comparison`
>
> Il y a en effet une limite au nombre de fois qu'une fonction peut s'appeler elle-même avant de terminer. (Dans d'autres langages que Python, on peut contourner cette limite, au prix d'une petite ré-écriture de la fonction, voir "tail-recursion" sur Wikipedia; mais en Python, comme dans beaucoup de langages, c'est impossible.) Cette limite est tout de même très élevée, et en pratique ça ne dérange pas trop.
>
> Ceci dit, dans cet exercice on vous demande d'écrire une version de `factorielle` sans récursion (avec une boucle), et de comparer la vitesse et les plantages.



## 2 - Une étude de cas : nombres de Stirling et dictionnaires

Les *nombres de Stirling de première espèce* sont par définitions les entiers $s(n,k)$ définis par l'identité polynomiale :

$x(x-1)(x-2)\cdots (x-n+1) = \sum_{k=0}^n s(n,k) x^k$.

Autrement dit: par définition $s(n,k)$ est le coefficient de $x^k$ quand on développe le polynôme donné par le membre de gauche de cette équation. Mais nous n'allons pas nous servir de cette définition pour faire les calculs.

En effet, on peut montrer que $s(n,k) = (-1)^{n-k} c(n,k)$ où $c(n,k)$ est positif, et surtout vérifie les identités suivantes :

 * $c(0,0) = 1$,
 * $c(n,0)=0$ pour $n>0, \quad$       $c(0,k)=0$ for $k>0$,
 * $c(n+1,k) = n c(n,k) + c(n,k-1)$.



>**Exercice (Stirling 1)** Ecrire une fonction récursive `stirling(n,k)` qui calcule $c(n,k)$ à partir des formules ci-dessus. Puis, étudier ses limitations : problèmes éventuels avec les grandes valeurs de $n$ et $k$, vitesse.

Un problème évident avec cette façon de faire est qu'on va répéter le calcul de certains $c(n,k)$ : par exemple pour calculer $c(4,4)$, on va calculer $c(4,3)$ et $c(3,4)$, et chacun de ces calculs va devoir trouver $c(3,3)$...

On va améliorer un peu les choses à l'aide d'un *dictionnaire*. C'est un objet Python qui peut en contenir d'autres, un peu comme une liste ; la différence, c'est que si `L` est une liste de longueur $n$, alors elle contient les objets `L[i]` où `i` est un entier entre $0$ et $n-1$, alors que pour un dictionnaire `D`, l'ensemble des indices `i` tels que `D[i]` a un sens peut être arbitraire ou presque. On construit cet ensemble d'indices -- que l'on appelle les *clefs* du dictionnaire -- en même temps que `D` lui-même.

In [ ]:
D= {}                   # création d'un dictionnaire vide
D[5]= "bonjour"         # 5 est maintenant une clef
D["toto"]= -1           # toto est maintenant une clef
print(D)

In [ ]:
D[5]

In [ ]:
[clef for clef in D]

In [ ]:
18 in D  # 18 est-il une clef?

Pour créer tout de suite un dictionnaire non-vide, on peut faire comme ceci :

In [ ]:
D= { (1,2,3) : "du texte", 7 : -4, "a" : "b"  }
print(D)

Notons que `(1,2,3)` a été utilisé comme clef. C'est un exemple de *tuple* (prononcé "teupeul", parfois traduit "p-uplet" en français). C'est presque la même chose qu'une liste (mais ce n'est pas une liste, notez les parenthèses au lieu des crochets). Nous ne voulons pas entrer dans les détails dans ce cours, donc nous retiendrons simplement ceci : un tuple se comporte comme une liste non-mutable (= non-modifiable). L'avantage des tuples sur les listes, c'est justement qu'on peut les utiliser comme clefs dans les dictionnaires! 

D'une manière générale, les clefs d'un dictionnaire ne doivent pas être mutables.

Voici encore une autre syntaxe : `dict( (clef(x), valeur(x)) for x in (quelque chose) )`. Par exemple :

In [ ]:
# dictionnaire des racines carrées d'entiers qui sont également des entiers :
N= 10
racines= dict(  (n**2, n) for n in range(N)   )   
print(racines)

In [ ]:
racines[9]

Et il y a même une syntaxe spéciale dans le cas où toutes les clefs sont des chaînes de caractères (notons qu'aucune de ces syntaxes "raccourcies" n'est vraiment utile pour nous, dans nos exemples) :

In [ ]:
notes_au_TP= dict(kevin= 12, whitney= 6, robert= 10)

In [ ]:
notes_au_TP

>**Exercice (Stirling 2)** Créer un dictionnaire `table_stirling` vide, puis une fonction `stirling2(n,k)` qui calcule $c(n,k)$ en stockant les résultats dans le dictionnaire au fur et à mesure, pour ne pas avoir à les re-calculer la prochaine fois qu'on appelle la fonction.
>
>Comparer la vitesse.